# 🌤️ W04 Lab: From NumPy to Pandas (SOLUTIONS)

**DS105A W04 LAB – Data Science for the Social World (Autumn Term 2025/2026)**

<div style="font-family: system-ui; padding: 20px 30px 20px 20px; background-color: #FFFFFF; border-left: 8px solid #ED9255; border-radius: 8px; box-shadow: 0 4px 12px rgba(0, 0, 0, 0.1);max-width:600px;color:#212121;">

**Lab Practice Notebook - SOLUTIONS**

- 📅 Date: 24 October 2025
- 👤 Name: [Your name] (🧑‍✈️ Pilot)
- 👤 Name: [Your partner's name] (🙋 Copilot)
- 🎯 Purpose: Compare NumPy and Pandas approaches to complex data classification

<span style="display:block;line-height:1.15em;color:#666666;font-size:0.9em;">

🥅 **Learning Goals**

 i) Experience the limitations of nested `np.where()` operations,
 ii) Use Pandas vectorised boolean operations for complex logic,
 iii) Chain multiple conditions with `&` and `|` operators,
 iv) Apply conditional logic to create new DataFrame columns efficiently.

</span>

</div>

## 📋 Before You Start

Make sure you have:
- ✅ Completed the 📝 **W04 Practice** (or most of it!)
- ✅ Attended yesterday's 🖥️ **W04 Lecture** on vectorisation
- ✅ Found a partner for pair programming today

**Pair Programming Roles:**
- 🧑‍✈️ **Pilot**: The person typing the code
- 🙋 **Copilot**: The person guiding and checking the code

You'll swap roles between Part I and Part II!

## ⚙️ Library Imports

In [ ]:
import json
import numpy as np
import pandas as pd

print("✅ Libraries loaded successfully!")

## 🌡️ Loading the Data

We have weather data for London during Summer 2024 (June through August).

This dataset includes **temperature** AND **rainfall** because today's classification task needs both variables.

In [ ]:
# Load weather data from JSON file
with open('data/london_summer_2024_weather.json', 'r') as f:
    weather_data = json.load(f)

# Extract the data we need
temperatures = weather_data['daily']['temperature_2m_max']
rainfall = weather_data['daily']['rain_sum']
dates = weather_data['daily']['time']

print(f"✅ Loaded {len(dates)} days of summer weather data")
print(f"📅 Date range: {dates[0]} to {dates[-1]}")
print(f"🌡️  Temperature range: {min(temperatures):.1f}°C to {max(temperatures):.1f}°C")
print(f"🌧️  Rainfall range: {min(rainfall):.1f}mm to {max(rainfall):.1f}mm")

## 🗺️ Today's Challenge: Weather Classification

Your task is to classify each summer day into one of these categories:

| Category | Temperature | Rainfall |
|----------|-------------|----------|
| Hot & Dry | > 25°C | < 1mm |
| Hot & Wet | > 25°C | ≥ 1mm |
| Mild & Dry | 20-25°C | < 1mm |
| Mild & Wet | 20-25°C | ≥ 1mm |
| Cool | < 20°C | any |

**The twist:** You'll implement this **twice**:
1. First with NumPy's nested `np.where()` (you'll struggle - that's intentional!)
2. Then with Pandas vectorised operations using named boolean columns (much cleaner!)

---

# Part I: The NumPy Approach (🧑‍✈️ Pilot = First Person)

In this part, you'll try to classify the weather using nested `np.where()` calls.

This is deliberately challenging. The goal is to experience the pain of complex nested conditionals!

## Step 1: Create NumPy Arrays

In [ ]:
# Convert Python lists to NumPy arrays
temps_array = np.array(temperatures)
rain_array = np.array(rainfall)

print(f"Arrays created:")
print(f"  Temperatures: {temps_array.shape}, dtype={temps_array.dtype}")
print(f"  Rainfall: {rain_array.shape}, dtype={rain_array.dtype}")

## Step 2: Understanding `np.where()`

Before tackling the complex version, let's practice with a simple example.

In [ ]:
# Simple example: Is it hot?
is_hot = np.where(temps_array > 25, "Hot", "Not Hot")

print("First 10 classifications:")
for i in range(10):
    print(f"{dates[i]}: {temps_array[i]:>5.1f}°C → {is_hot[i]}")

**🙋 Copilot:** Explain to your pilot what `np.where()` does. How is it different from a regular `if-else` statement?

## Step 3: The Challenge - Nested `np.where()`

Now comes the hard part. You need to classify days based on **BOTH** temperature and rainfall.

**🧑‍✈️ Pilot:** Try to implement the classification logic below. Use the table above as your guide.

**🙋 Copilot:** Help your pilot think through the logic. What should the outermost condition check?

In [ ]:
# TODO: Implement the nested np.where() classification
# Hint: Start with temperature, then within each temperature category, check rainfall

weather_type_numpy = np.where(
    temps_array > 25,
    np.where(rain_array < 1, "Hot & Dry", "Hot & Wet"),
    np.where(
        temps_array >= 20,
        np.where(rain_array < 1, "Mild & Dry", "Mild & Wet"),
        "Cool"
    )
)

## Step 4: Verify Your Results

In [ ]:
# Check the first 15 summer days
print("First 15 summer days classified:")
print("-" * 70)
for i in range(15):
    print(f"{dates[i]}: {temps_array[i]:>5.1f}°C, {rain_array[i]:>5.2f}mm → {weather_type_numpy[i]}")

In [ ]:
# Count each category
unique, counts = np.unique(weather_type_numpy, return_counts=True)
print("\nWeather distribution:")
for i in range(len(unique)):
    category = unique[i]
    count = counts[i]
    print(f"{category:>15}: {count:>3} days ({count/len(weather_type_numpy)*100:>5.1f}%)")

## Step 5: Reflect on the Experience

🙋 **Copilot:** Answer these questions together:

1. How easy was it to write the nested `np.where()` code?
2. How easy is it to **read** the code now that it's written?
3. If you needed to add a "Very Hot" category (> 30°C), how hard would that be?
4. Could you debug this code easily if it had a mistake?

Write your thoughts here:

- [*Your reflections here*]

---

# Part II: The Pandas Vectorisation Solution (🙋 Copilot = Now the Pilot!)

**⚠️ SWAP ROLES!** The Copilot from Part I is now the Pilot.

In this part, you'll solve the same problem using Pandas DataFrames with vectorised boolean operations. You'll see how breaking down complex logic into named boolean columns makes your code much clearer!

## Step 1: Create a DataFrame

In [ ]:
# Build a structured DataFrame
weather_df = pd.DataFrame({
    'date': dates,
    'temp': temperatures,
    'rain_mm': rainfall
})

print("DataFrame created:")
print(f"Shape: {weather_df.shape}")
print(f"\nFirst 10 rows:")
weather_df.head(10)

**🙋 New Copilot:** What's the advantage of having a DataFrame instead of separate arrays?

## Step 2: Create Boolean Condition Columns

Instead of nesting conditionals, create explicit boolean columns for each condition.

In [ ]:
# Create boolean columns for temperature categories
weather_df['is_hot'] = weather_df['temp'] > 25
weather_df['is_mild'] = (weather_df['temp'] >= 20) & (weather_df['temp'] <= 25)
weather_df['is_cool'] = weather_df['temp'] < 20

# Create boolean column for rainfall
weather_df['is_dry'] = weather_df['rain_mm'] < 1

# Look at the result
print("DataFrame with boolean columns:")
weather_df.head(15)

**Key insight:** Notice how readable these boolean columns are! Each condition has a clear name. You can inspect each column separately to verify your logic.

## Step 3: Build the Classification Using Boolean Columns

Now use these boolean columns to create the classification using `np.select()`.

**📖 New concept:** `np.select()` takes a list of conditions and corresponding labels.

In [ ]:
# Build lists of conditions and corresponding choices
conditions = [
    weather_df['is_hot'] & weather_df['is_dry'],    # Hot & Dry
    weather_df['is_hot'] & ~weather_df['is_dry'],   # Hot & Wet
    weather_df['is_mild'] & weather_df['is_dry'],   # Mild & Dry
    weather_df['is_mild'] & ~weather_df['is_dry'],  # Mild & Wet
    weather_df['is_cool']                            # Cool
]

choices = [
    'Hot & Dry',
    'Hot & Wet',
    'Mild & Dry',
    'Mild & Wet',
    'Cool'
]

# Use np.select to create the classification
weather_df['weather_type'] = np.select(conditions, choices)

# Check the result
print("Classification complete!")
weather_df[['date', 'temp', 'rain_mm', 'weather_type']].head(20)

**🙋 New Copilot:** Compare this to the nested `np.where()` from Part I. Notice how the conditions and choices line up clearly. Which is easier to read? Which would be easier to debug if there was a mistake?

## Step 4: Verify Results Match NumPy Approach

In [ ]:
# Compare with the NumPy approach from Part I
numpy_result = weather_type_numpy
pandas_result = weather_df['weather_type'].values

matches = (numpy_result == pandas_result).all()

print(f"Do both approaches give the same classifications? {matches}")

if matches:
    print("✅ Perfect! Both approaches produced identical results.")
else:
    print("❌ There's a discrepancy. Check your logic!")
    
# Show first 15 comparisons
print("\nFirst 15 comparisons:")
comparison_df = pd.DataFrame({
    'date': dates[:15],
    'temp': temperatures[:15],
    'rain': rainfall[:15],
    'NumPy': numpy_result[:15],
    'Pandas': pandas_result[:15],
    'Match': (numpy_result[:15] == pandas_result[:15])
})
print(comparison_df)

## Step 5: Count and Analyse Categories

In [ ]:
# Count each category
print("Weather distribution:")
print(weather_df['weather_type'].value_counts())

# Calculate percentages
print("\nPercentages:")
print(weather_df['weather_type'].value_counts(normalize=True) * 100)

In [ ]:
# Show a few examples from each category
print("\nExamples from each category:")
print("=" * 70)

for category in weather_df['weather_type'].unique():
    print(f"\n{category}:")
    examples = weather_df[weather_df['weather_type'] == category][['date', 'temp', 'rain_mm']].head(3)
    print(examples)

## Step 6: Final Reflection

**Both of you:** Discuss and write down your answers:

1. How did breaking down the logic into named boolean columns help?
2. Which approach (nested `np.where()` vs boolean columns) would you prefer for a real project?
3. What if you needed to add a new variable (like wind speed) to the classification?
4. What if you needed to change the temperature threshold from 25°C to 28°C?

Your thoughts:

- [*Your reflections here*]

---

# Optional Extension: More about `np.select()`

**Why is `np.select()` useful?**

Unlike nested `np.where()`, `np.select()` lets you:
- List all conditions clearly in one place
- Match each condition to its label explicitly
- Add a default value for cases that don't match any condition

**The pattern:**
```python
conditions = [condition1, condition2, condition3]  # List of boolean arrays
choices = ['Label1', 'Label2', 'Label3']           # Corresponding labels
result = np.select(conditions, choices, default='Other')
```

**How it works:**
1. Checks the first condition - if True, assigns first choice
2. If False, checks the second condition - if True, assigns second choice
3. And so on...
4. If none match, assigns the default value

This is why **order matters** - more specific conditions should come first!

---

# Bonus Challenge (If You Have Time)

Try extending the classification to include a humidity dimension!

## Bonus: Add Humidity Classification

In [ ]:
# Create fake humidity data
np.random.seed(42)
humidity = np.random.uniform(40, 90, len(weather_df))
weather_df['humidity'] = humidity

# Create boolean column for humidity
weather_df['is_comfortable'] = weather_df['humidity'] < 60

# Use np.select to add comfort information to weather type
comfort_conditions = [
    weather_df['is_comfortable'],
    ~weather_df['is_comfortable']
]

comfort_choices = [
    weather_df['weather_type'] + ' (Comfortable)',
    weather_df['weather_type'] + ' (Humid)'
]

weather_df['detailed_type'] = np.select(comfort_conditions, comfort_choices)

# Show a few examples
print("Weather with comfort information:")
print(weather_df[['date', 'temp', 'rain_mm', 'humidity', 'detailed_type']].head(15))

In [ ]:
# Identify perfect summer days (22-28°C AND < 0.5mm rain AND < 60% humidity)
weather_df['is_perfect_day'] = (
    (weather_df['temp'] >= 22) & 
    (weather_df['temp'] <= 28) & 
    (weather_df['rain_mm'] < 0.5) & 
    weather_df['is_comfortable']
)

# Show perfect days
print("\nPerfect Summer Days:")
perfect_days = weather_df[weather_df['is_perfect_day']][['date', 'temp', 'rain_mm', 'humidity']]
print(f"\nFound {len(perfect_days)} perfect days!")
print(perfect_days.head(10))

---

# Summary

Today you experienced:

1. ✅ The difficulty of nested `np.where()` for complex logic (Part I)
2. ✅ How named boolean columns make logic transparent (Part II)
3. ✅ Vectorised operations for efficient data processing
4. ✅ The readability advantage of breaking down complex conditions

**Key Takeaway:** For complex logic, creating named boolean columns in Pandas is almost always clearer and more maintainable than nested NumPy conditionals!

## What's Next?

- **Mini-Project 1** was released yesterday - you now have all the skills you need!
- **Next week (W05):** Advanced data transformations and seaborn visualisation
- **Week 06 (Reading Week):** Focus time to complete Mini-Project 1

Great work today! 🎉